In [4]:
import tensorflow

In [5]:
import pandas as pd
def filesave(dataframe,name):
    dataframe.to_csv(name,sep="\t", encoding="utf-8",index=False)
def fileread(name):
    return pd.read_csv(name,sep="\t",encoding="utf-8")

In [6]:
test=fileread('joongang_dataframe.csv')

In [7]:
test.drop_duplicates(inplace=True)

In [8]:
len(test)

110482

In [10]:
from tensorflow.keras.models import load_model
from konlpy.tag import Okt
import pickle
from tensorflow.keras.preprocessing.sequence import pad_sequences
from collections import Counter

stopwords = ['도', '는', '다', '의', '가', '이', '은', '한', '에', '하', '고', '을', '를', '인', '듯', '과', '와', '네', '들', '듯', '지', '임', '게']
max_len = 42


with open("senti_tokenizer.pickle","rb") as fr:
    tokenizer = pickle.load(fr)

loaded_model = load_model('LSTMGRU.h5')

okt=Okt()

In [11]:

def predict_text(text):
    new_text = okt.morphs(text, stem=True)
    new_text = [word for word in new_text if not word in stopwords]
    encoded = tokenizer.texts_to_sequences([new_text])
    pad_encoded_text = pad_sequences(encoded,maxlen=max_len)
    score = float(loaded_model.predict(pad_encoded_text))
    return score

def predict_senti(text):
    idx2label={0:"부정",1:"긍정"}
    score_list=[]
    for i in text:
        if len(i)<6:
            continue
        score_list.append(idx2label[round(predict_text(i))])
    return score_list

def predict_senti2(text):
    idx2label={0:"부정",1:"긍정",-1:"중립"}
    score_list = []
    for i in text:
        if len(i)<6:
            continue
        score = predict_text(i.strip())
        if score >= 0.7:
            label = 1
        elif score <= 0.3:
            label = 0
        else:
            label = -1
        score_list.append(idx2label[label])
    return score_list



In [12]:
cnt=0
for i in range(len(test)):
    print((test.iloc[i])['title'])
    print("----")
    cnt+=1
    if cnt>10:
        break

“시장 왜곡돼 집값 상승세 지속, 내년 대선이 분수령”
----
'저녁 있는 삶' 이런 카피 없나···섹시 고집하다 당한 與주자들
----
[단독]"대역 아니냐" 확 달라진 전두환, 알고보니 혈액암
----
美 Z세대가 中 쇼핑몰에 갇혔다…자라·H&M 제낀 쉬인SHEIN
----
김의겸 선배 행복하십니까…외신이 묻네요 "이게 무슨 법이냐" [뉴스원샷]
----
'골목식당' 방영 후 반년…성남시 모란역 뒷골목 근황 보니
----
'영원한 증언자' 위안부 할머니들 되살린 할리우드 출신 교수
----
A380 멸종, 하늘길 공룡시대의 종말…항공기도 '가성비 시대' [뉴스원샷]
----
'알라븅♡' 문자 진짜였지만…경찰은 '첫 성관계' 들여다본다 [사건추적]
----
[더오래] 그 여름날, 우리 달콤쌉싸름했던 첫사랑의 추억
----
전국서 비행기 타고 온다···제주 산부인과 수상한 영업비밀
----


In [13]:
c=test.to_dict('records')

In [15]:
temp_df=fileread("joongang_senti_df.csv")

In [18]:
# 처음에 리셋 할 때만 돌리기
temp_df = pd.DataFrame(columns=test.columns)
filesave(temp_df,"joongang_senti_df.csv")

In [ ]:
count=0
for i in range(count//100,(len(c)//100) +1):
    for j in range(count,count+100):
        if j >= len(c):
            break
        sentence = (c[j])['title']
        tempdict = c[j]
        tempdict['title_senti'] = predict_text(str(sentence))
        temp_df=temp_df.append(tempdict,ignore_index=True)
    filesave(temp_df,"joongang_senti_df.csv")
    print(count+100,"까지 감정 분석 후 저장")
    count+=100

1/1 [==============================] - ETA: 0s

C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)


1/1 [==============================] - 0s 17ms/step


C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)


1/1 [==============================] - ETA: 0s

...

1/1 [==============================] - 0s 24ms/step


C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)


1/1 [==============================] - 0s 25ms/step


C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)
C:\Users\Public\Documents\ESTsoft\CreatorTemp\ipykernel_14896\3790010354.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  temp_df=temp_df.append(tempdict,ignore_index=True)


1/1 [==============================] - 0s 57ms/step


In [25]:
temp_df['title'].nunique()

59415

In [26]:
joongang_senti_df = fileread("joongang_senti_df.csv")

In [27]:
joongang_senti_df

title  \
0           “NLL 침범 ‘무포호’, 과거 제3국서 등록 취소…최근까지 중국 입항” VOA   
1                   北, 中당대회 끝나자 서해NLL 도발… 7차 핵실험 ‘명분 쌓기’   
2                          檢, 민주硏 압수수색-정진상 출금… 민주 “野 말살”   
3                         이재명 “대장동 특검, 尹관련 저축銀 부분 빼도 좋다”   
4      민주당, 오늘 尹대통령 국회 시정연설 보이콧… 尹 “시정연설에 조건, 헌정사서 들어...   
...                                                  ...   
59797                          펠레 위에 메시… 남미 A매치 79골 최다득점   
59798                            ‘현대가 더비’ 울산-전북, 득점없이 비겨   
59799                         펠레 넘어선 메시, 남미 A매치 79골 최다득점   
59800                     “환골탈태가 필요하다”…국가대표 선수단 코치들 한목소리   
59801                   “어제는 찝찝했는데…” 몸 풀린 박인비, 공동 18위 도약   

                                                 content               date  \
0      \n서해 북방한계선(NLL)을 침범했다 퇴각한 북한 상선 ‘무포호’가 과거 토고 등...   2022-10-25 06:58   
1      \n먼저 월선하고도 “南이 도발” 트집\r\n北, 완충해역 포격… 9·19합의 위반...   2022-10-25 03:00   
2      \n檢, 김용 쓰던 PC서 문서파일 확보\r\n이틀째 金 불러 8억 용처 등 조사\...   2022-10-25 03:00   
3      \n“김건희 특검과 무관” 수위 낮추며\r\n본인 수사 ‘檢 아닌 특검’ 뜻 내비쳐...   2022-10-25 03:00   
4      \n박홍근 “당사 침탈 사과요구 무시”\r\n정진석 “시정연설은 국민 위한 것”\n...   2022-10-25 03:00   
...                                                  ...                ...   
59797  \n리오넬 메시(왼쪽에서 두 번째)가 10일 아르헨티나 부에노스아이레스에서 열린 2...   2021-09-11 03:00   
59798  \n1위 울산-2위 전북 승점 차 4 유지\r\n대구는 포항 2-1로 꺾고 3위 올...   2021-09-11 03:00   
59799  \n‘축구의 신’ 리오넬 메시(34·아르헨티나)가 ‘축구 황제’ 펠레(81·브라질)...   2021-09-10 21:10   
59800  \n‘한국 엘리트 스포츠의 환골탈태가 필요하다.’ 최근 열린 2020 도쿄 올림픽과...   2021-09-10 20:28   
59801  \n적응을 마친 ‘골프 여제’ 박인비(KB금융그룹)가 한국여자프로골프(KLPGA) ...   2021-09-10 20:00   

        section                                                url  \
0      Politics  https://www.donga.com/news/Politics/article/al...   
1      Politics  https://www.donga.com/news/Politics/article/al...   
2      Politics  https://www.donga.com/news/Politics/article/al...   
3      Politics  https://www.donga.com/news/Politics/article/al...   
4      Politics  https://www.donga.com/news/Politics/article/al...   
...         ...                                                ...   
59797    Sports  https://www.donga.com/news/Sports/article/all/...   
59798    Sports  https://www.donga.com/news/Sports/article/all/...   
59799    Sports  https://www.donga.com/news/Sports/article/all/...   
59800    Sports  https://www.donga.com/news/Sports/article/all/...   
59801    Sports  https://www.donga.com/news/Sports/article/all/...   

       title_senti  
0         0.148715  
1         0.678253  
2         0.087201  
3         0.916447  
4         0.677403  
...            ...  
59797     0.860008  
59798     0.613999  
59799     0.848213  
59800     0.888905  
59801     0.050455  

[59802 rows x 6 columns]

In [44]:
# 높은 긍정 점수를 받은 기사 타이틀 뽑아보기
ttt=joongang_senti_df[joongang_senti_df['title_senti']>0.9]['title']
from random import randint
for _ in range(5):
    r=randint(0, len(ttt)-1)
    print(ttt.iloc[r])

‘청년 귀농’ 작년 1507가구 역대 최다
‘이터널스’ 개봉 첫 주 161만명…올해 최고 흥행 노린다
스타벅스, 친환경 커피 퇴비 누적 생산 1000만 포대 돌파 예상
콘테 감독 “한국에서 위대한 경험, 모든 것이 고맙다”
김갑수, 장민호 데뷔 첫 콘서트에 함께 ‘울컥’…父 위한 감동 무대


In [45]:
# 낮은 점수를 받은 기사 타이틀 뽑아보기
filter_df = joongang_senti_df[joongang_senti_df['title_senti']<0.1]['title']
for _ in range(5):
    r=randint(0, len(ttt)-1)
    print(filter_df.iloc[r])

bhc, BBQ 상대 손배소 패소…BBQ “악의적 소송에 유감”
김소현 “뮤지컬서 1년에 160회 죽어, 안 죽으면 허전”
대법 “스토킹범 불구속 때 ‘조건부 석방제’ 도입해야…전자장치 부착”
英여왕 ‘세기의 장례식’, 세계 정상·왕족만 500여명…시진핑·푸틴은 불참
김태형 두산 감독 “최원준·곽빈·이영하 등 토종 선발 선전”
